# TEAM - SASA
## POC and Initial EDA for Rapper Website

In [1]:
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
from selenium.webdriver.common.action_chains import ActionChains

from time import sleep

import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt 

In [2]:
!which chromedriver

/usr/local/bin/chromedriver


## HELPER FUNCTIONS

In [3]:
urls = []

def get_total_pages(driver):
    pages = driver.find_elements(By.CSS_SELECTOR, 'div.gsc-cursor-page')
    return len(pages)

def get_urls(driver, page):
    print(f'Start crawling article URLs for page {page}...')
    alinks = driver.find_elements(By.CSS_SELECTOR, 'a.gs-title')
    for a in alinks:
        link = a.get_attribute('href')
        if (link != None) and (link not in urls):
            urls.append(link)
    print('Done.')

def get_pages(driver, totalpages):
    print(f'Total number of pages to crawl: {totalpages}', end='\n\n')
    # Page 1
    get_urls(driver, 1)
    # Page 2 onwards
    driver.maximize_window()
    for p in range(1, totalpages):
        driver.execute_script('window.scrollBy(0, document.body.scrollHeight)', '') 
        pages = driver.find_elements(By.CSS_SELECTOR, 'div.gsc-cursor-page')
        pages[p].click()
        sleep(5)
        get_urls(driver, p+1)

def close_popups():
    try:
        driver.find_element(By.XPATH, '//*[@id="survicate-box"]/div/div/div[3]/div[2]/button').click()
    except:
        pass
    try:
        driver.find_element(By.XPATH, '//*[@id="onesignal-slidedown-cancel-button"]').click()
    except:
        pass
    try:
        # Close footer ads
        driver.find_element(By.XPATH, '//*[@id="__next"]/div/div[16]//following::div/p/span').click()
    except:
        pass

def get_url_data(driver, url):
    ### PREPARE ARTICLE URL
    driver.get(url)
    sleep(15)

    ### PREPARE TITLE
    title = driver.find_element(By.XPATH, '//*[@id="__next"]/div/div[16]/div[5]/div[2]/div[2]/div/div/h1')
    title = title.text
    print(f'\n[Title]\n{title}')

    ### PREPARE PUBLISHED DATE
    pubdate = driver.find_element(By.XPATH, '//*[@id="__next"]/div/div[16]/div[5]/div[2]/div[2]/div/div/p/time')
    pubdate = pubdate.text
    print(f'\n[Date Pulished]\n{pubdate}')

    ### PREPARE AUTHOR NAME
    author = driver.find_element(By.XPATH, '//*[@id="__next"]/div/div[16]/div[5]/div[2]/div[3]/div/a')
    author = author.text
    print(f'\n[Author]\n{author}')

    # Try closing popups before clicking 'SEE THE RESULTS' button
    sleep(2)
    close_popups()

    ### PREPARE ARTICLE CONTENT
    article = driver.find_element(By.XPATH, '//*[@id="__next"]/div/div[16]/div[6]')
    article_content = article.text.replace('ADVERTISEMENT','').replace('How did this story make you feel?', '').replace('INSPIRED','')\
        .replace('HAPPY','').replace('AMUSED','').replace('NEUTRAL','').replace('ANNOYED','').replace('SAD','').replace('ANGRY','')\
        .replace('AFRAID','').replace('SEE THE RESULTS','').replace(' \n','').replace('\n ','').replace('\n\n','').replace('  ','') 
    print(f'\n[Content]\n{article_content}')

    ### PREPARE SENTIMENT RESULTS
    # Scroll to 'SEE THE RESULTS' button then simulate click to get sentiment results
    sleep(3)
    sentiment_classname = driver.find_element(By.XPATH, '//*[@id="__next"]/div/div[16]/div[6]/div[4]/following::div').get_attribute('class')
    driver.execute_script(f'document.getElementsByClassName("{sentiment_classname}").scrollIntoView', '')
    
    # Automate click event to get sentiment results
    sentiment_index = 0
    for i in range(100):
        try:
            btn_sentiment = driver.find_element(By.XPATH, f'//*[@id="__next"]/div/div[16]/div[6]/div[4]/div[{i}]/div/div/span')
            if btn_sentiment.text.upper() == 'SEE THE RESULTS':
                sleep(2)
                close_popups()
                action = ActionChains(driver)
                action.move_to_element(btn_sentiment).click().perform()
                # btn_sentiment.click()
                sentiment_index = i
                break
        except:
            pass

    sleep(3)
    # Clean some sentiment texts
    sentiment_results = driver.find_element(By.XPATH, f'//*[@id="__next"]/div/div[16]/div[6]/div[4]/div[{sentiment_index}]/div')
    sentiment_results = sentiment_results.text.replace('HOW OTHERS ARE FEELING', '').replace(' \n','').replace('\n ','').replace(' ARE ','-')
    # Convert each line of sentiment text to a list item
    sentiment_results = list(filter(None, sentiment_results.split('\n')))
    # Make a key-value pair of sentiment text and store it as dictionary object
    sentiment_results = {s.split('-')[1] : float(s.split('-')[0].split('%')[0])*.01 for s in sentiment_results}
    # Add a 0% value for sentiment key that does not have results in the current article and store as 'other sentiments'
    sentiment_keys = ['INSPIRED', 'HAPPY', 'AMUSED', 'NEUTRAL', 'ANNOYED', 'SAD', 'ANGRY', 'AFRAID']
    sentiment_others = {k : 0. for k in sentiment_keys if k not in sentiment_results}
    # Combine 'other sentiment dictionary' to the 'sentiment result dictionary' 
    sentiment_results = {**sentiment_results, **sentiment_others}
    print(f'\n[Sentiment]')
    print(sentiment_results)

    ### GET SENTIMENT RESULTS FROM ARTICLE
    return {'urls':url, 'titles':title, 'authors':author, 'published_dates':pubdate, 'articles_content':article_content, 'sentiments':sentiment_results}
    

# WEB SCRAPING

In [4]:
DRIVER_PATH = '/usr/local/bin/chromedriver'
SEARCH_URL = 'https://r3.rappler.com/?option=com_rappler&task=search&language=english&q=philippines+covid+vaccine'

driver = webdriver.Chrome(DRIVER_PATH)
driver.get(SEARCH_URL)

dataset = []

totalpages = get_total_pages(driver)
get_pages(driver, totalpages)
print(f'\nTotal number of articles: {len(urls)}')

for i,url in enumerate(urls):
    # try:
    print(f'\n\n\n[{i+1}]{" ":>5}SCRAPING DATA  ~>  {url}')
    data = get_url_data(driver, url)
    dataset.append(data)
    # except Exception as e:
    #     print(f'SCRAPING ERROR: {e}')

driver.quit()
df = pd.DataFrame(dataset)
df

Total number of pages to crawl: 10

Start crawling article URLs for page 1...
Done.
Start crawling article URLs for page 2...
Done.
Start crawling article URLs for page 3...
Done.
Start crawling article URLs for page 4...
Done.
Start crawling article URLs for page 5...
Done.
Start crawling article URLs for page 6...
Done.
Start crawling article URLs for page 7...
Done.
Start crawling article URLs for page 8...
Done.
Start crawling article URLs for page 9...
Done.
Start crawling article URLs for page 10...
Done.

Total number of articles: 97



[0]     SCRAPING DATA  ~>  https://www.rappler.com/newsbreak/explainers/why-covid-19-vaccines-not-arrive-philippines

[Title]
Here’s why COVID-19 vaccines haven’t arrived in the Philippines yet

[Date Pulished]
FEB 18, 2021 9:22 AM PHT

[Author]
SOFIA TOMACRUZ

[Content]
MANILA, PHILIPPINES
The Philippine government needs a key measure on indemnification funds to be signed into law
Philippine pandemic officials announced the delivery of the count

NoSuchElementException: Message: no such element: Unable to locate element: {"method":"xpath","selector":"//*[@id="__next"]/div/div[16]/div[5]/div[2]/div[2]/div/div/p/time"}
  (Session info: chrome=89.0.4389.72)


In [5]:
df

urls  \
0  https://www.rappler.com/newsbreak/explainers/w...   

                                              titles         authors  \
0  Here’s why COVID-19 vaccines haven’t arrived i...  SOFIA TOMACRUZ   

            published_dates  \
0  FEB 18, 2021 9:22 AM PHT   

                                    articles_content  \
0  MANILA, PHILIPPINES\nThe Philippine government...   

                                          sentiments  
0  {'ANGRY': 0.42, 'ANNOYED': 0.23, 'SAD': 0.11, ...

In [3]:
from IPython.display import Video, HTML

Video('team-sasa.mp4', embed=True, html_attributes='muted loop autoplay', width=600 he)
# HTML('''
#     <center>
#     <div width="300" height="160" >
#         <video controls>
#             <source src="team-sasa.webm" type="video/webm">
#         </video>
#     </div>
# ''')

In [18]:
!pwd

/Users/rodelarenas/Desktop/ESKWELABS_COHORT/_SPRINTS/04-NLP/3-01-Intro/c6_sprint4
